In [1]:
huggiingface_repo_id = 'Qi28/SD_QZ'  # 替换为你的 Hugging Face 数据集 ID
huggiingface_path = 'frp'
download_path = '/tmp/code/frp' 
#NPS_key = 'n0i25dzqfsvr7bdd'
#nezha_agent_key = 'L3USpU8bbpHRV90uuC'
#sd_url = 'http://43.134.133.34:7788'
#!export CUDA_VISIBLE_DEVICES=0,1

import requests
import subprocess
import threading
import shutil
import zipfile
import os
import time
import json  # 导入 json 模块
from requests.adapters import HTTPAdapter
from requests.packages.urllib3.util.retry import Retry
from IPython.display import HTML, display
import configparser
!rm /tmp/code/config.ini
!wget -O /tmp/code/config.ini 'https://hf-mirror.com/datasets/Qi28/SD_QZ/resolve/main/config.ini'
config = configparser.ConfigParser()
config.read('/tmp/code/config.ini')
frp_status = config.getint('server', 'frp_status')
nps_status = config.getint('server', 'nps_status')
sd_url = config.get('server', 'url')
NPS_key = config.get('server', 'NPS_key')
NPS_server = config.get('server', 'NPS_server')
nezha_agent_key = config.get('server', 'nezha_agent_key')
nezha_agent_url = config.get('server', 'nezha_agent_url')
print(f"frp_status: {frp_status}")
print(f"nps_status: {nps_status}")
print(f"sd_url: {sd_url}")
print(f"NPS_key: {NPS_key}")
print(f"NPS_server: {NPS_server}")
print(f"nezha_agent_key: {nezha_agent_key}")


--2024-11-22 02:55:46--  https://hf-mirror.com/datasets/Qi28/SD_QZ/resolve/main/config.ini
Resolving hf-mirror.com (hf-mirror.com)... 153.121.57.40, 160.16.199.204, 133.242.169.68
Connecting to hf-mirror.com (hf-mirror.com)|153.121.57.40|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 189 [text/plain]
Saving to: ‘/tmp/code/config.ini’

/tmp/code/config.in 100%[===================>]     189  --.-KB/s    in 0s      

2024-11-22 02:55:47 (2.65 MB/s) - ‘/tmp/code/config.ini’ saved [189/189]

frp_status: 0
nps_status: 1
sd_url: http://119.8.118.149:8000
NPS_key: q9wj1cnlek4j3hg5
NPS_server: 119.8.118.149:7001
nezha_agent_key: L3USpU8bbpHRV90uuC


In [2]:
# FRP  NPS
def Frpc():
    thread = threading.Thread(target=run_commands)
    thread.start()
    !rm /tmp/code/frp/*.ini
    # 定义 Hugging Face 数据集 ID
    api_url = f'https://hf-mirror.com/api/datasets/{huggiingface_repo_id}/tree/main/{huggiingface_path}' 

    # 获取文件列表
    response = requests.get(api_url)
    if response.status_code != 200:
        print(f'Error: Failed to fetch file list from {api_url}')
        response.raise_for_status()

    file_list = response.json()
    yun_files = [file['path'] for file in file_list if file['type'] == 'file']

    # 下载文件
    for yun_file in yun_files:
        url = f'https://hf-mirror.com/datasets/{huggiingface_repo_id}/resolve/main/{yun_file}' 
        response = requests.head(url)
        if response.status_code == 200:
            result = subprocess.run(['wget', '-O', os.path.join(download_path, os.path.basename(yun_file)), url, '-q'], capture_output=True)
            if result.returncode != 0:
                print(f'Error: Failed to download {yun_file} from {url}')
        else:
            print(f'Error: Invalid URL {url}')

    # 修改 frpc 可执行文件权限
    frpc_executable = '/tmp/code/frp/frpc'
    subprocess.run(['chmod', '+x', frpc_executable], check=True)

    # 启动 frpc 实例
    for yun_file in yun_files:
        frpini_path = os.path.join(download_path, os.path.basename(yun_file))
        print(f'运行FRP配置: {frpini_path}')
        subprocess.Popen([frpc_executable, '-c', frpini_path])

#Frpc()
# 创建和启动线程
#thread = threading.Thread(target=Frpc)
#thread.start()
def NPS():
    #NPS_commands = f"/tmp/code/nps/npc -server={NPS_server} -vkey={NPS_key} -type=tcp"
    run_commands3([f"/tmp/code/nps/npc -server={NPS_server} -vkey={NPS_key} -type=tcp"])
    #subprocess.Popen(NPS_commands, shell=True)

In [3]:
# SSH

def run_commands():
    #run_commands3(["apt update","apt install openssh-server -y","apt-get install vim -y","sudo sed -i '/PasswordAuthentication/s/^#//g' /etc/ssh/ssh_config","sudo sed -i '/PermitRootLogin prohibit-password/s/prohibit-password/yes/' /etc/ssh/sshd_config","systemctl restart ssh"])
    # 更新包列表
    run_command("apt update")
    #run_commands3(["apt update"])
    
    # 安装openssh-server
    run_command("apt install openssh-server -y")
    #run_commands3(["apt install openssh-server -y"])
    
    # 安装vim
    run_command("apt-get install vim -y")
    #run_commands3(["apt-get install vim -y"])
    
    # 配置SSH客户端
    config_client_cmd = "sed -i '/PasswordAuthentication/s/^#//g' /etc/ssh/ssh_config"
    run_command(config_client_cmd)
    #run_commands3(["sudo sed -i '/PasswordAuthentication/s/^#//g' /etc/ssh/ssh_config"])
    
    # 配置SSH服务端
    config_server_cmd = "sed -i '/PermitRootLogin prohibit-password/s/prohibit-password/yes/' /etc/ssh/sshd_config"
    run_command(config_server_cmd)
    #run_commands3(["sudo sed -i '/PermitRootLogin prohibit-password/s/prohibit-password/yes/' /etc/ssh/sshd_config"])
    
    # 重启SSH服务
    run_command("systemctl restart ssh")
    #run_commands3(["systemctl restart ssh"])
    
    # 设置root密码
    os.system("echo 'root:qilan' | chpasswd")
    
    # 修改PermitRootLogin
    os.system("echo 'PermitRootLogin yes' | tee -a /etc/ssh/sshd_config")
    
    # 重启ssh服务
    os.system("service ssh restart")
    
    # 更新LD_LIBRARY_PATH环境变量
    os.system("export LD_LIBRARY_PATH=$(echo $LD_LIBRARY_PATH | tr ':' '\n' | grep -v '/opt/conda/lib' | paste -sd ':') ")

def run_command(command):
    try:
        subprocess.run(command, check=True, shell=True)
    except subprocess.CalledProcessError as e:
        print(f"An error occurred: {e}")

# 创建并启动线程
#thread = threading.Thread(target=run_commands)
#thread.start()

# 等待线程完成
#thread.join()

In [4]:
# 哪吒面板
def run_script():
    !rm -r /tmp/code/nezha-agent
    # GitHub项目名和API URL
    project_name = "nezhahq/agent"
    releases_api_url = f"https://api.github.com/repos/{project_name}/releases"
    # 获取最新版本的信息
    response = requests.get(releases_api_url)
    if response.status_code == 200:
        releases = response.json()
        latest_version = releases[0]['tag_name']  # 假设最新版本是列表中的第一个
        print(f"Latest version: {latest_version}")
    else:
        print("Failed to fetch releases information.")
        exit()
    # 构造下载链接
    download_url = f"https://slink.ltd/https://github.com/{project_name}/releases/download/{latest_version}/nezha-agent_linux_amd64.zip"
    # 指定下载文件的保存路径
    zip_file_path = "/tmp/code/nezha-agent.zip"  # 临时ZIP文件路径
    # 确保下载目录存在
    os.makedirs(os.path.dirname(zip_file_path), exist_ok=True)
    # 发送HTTP GET请求下载文件
    response = requests.get(download_url, stream=True)
    # 检查请求是否成功
    if response.status_code == 200:
        # 打开文件进行写入
        with open(zip_file_path, 'wb') as file:
            for chunk in response.iter_content(chunk_size=128):
                file.write(chunk)
        print(f"Download completed. File saved to {zip_file_path}")
        # 解压ZIP文件
        with zipfile.ZipFile(zip_file_path, 'r') as zip_ref:
            zip_ref.extractall("/tmp/code/")
        print("Extraction completed.")
        # 可选：删除临时ZIP文件
        os.remove(zip_file_path)
        print(f"Removed temporary zip file: {zip_file_path}")
    else:
        print(f"Failed to download the file. Status code: {response.status_code}")
        print('启动哪吒面板')
    try:
        # 给予 nezha-agent 执行权限
        subprocess.run(["chmod", "+x", "/tmp/code/nezha-agent"], check=True)
        # 运行 nezha-agent 程序
        run_commands3([f"/tmp/code/nezha-agent -s {nezha_agent_url} -p {nezha_agent_key} -d"])
        #subprocess.run(["/tmp/code/nezha-agent", "-s", "nzzz.nwb.lol:5555", "-p", nezha_agent_key, "-d"], check=True)
    except subprocess.CalledProcessError as e:
        print(f"启动哪吒面板失败，错误内容: {e}")
# 创建和启动线程
#thread = threading.Thread(target=run_script)
#thread.start()

In [5]:
# 要清理的目录列表
directories_to_clean = [
    '/tmp/code/sd/outputs/txt2img-images',
    '/tmp/code/sd/outputs/imgmg-images',
]

def clean_directory():
    while True:
        for directory in directories_to_clean:
            # 检查目录是否存在
            if os.path.exists(directory):
                # 遍历目录中的所有内容（文件和子目录）
                for filename in os.listdir(directory):
                    file_path = os.path.join(directory, filename)
                    try:
                        # 检查是否为文件或文件夹，并尝试删除
                        if os.path.isfile(file_path) or os.path.isdir(file_path):
                            shutil.rmtree(file_path)
                            print(f"删除: {file_path}")
                    except FileNotFoundError:
                        # 如果文件或目录不存在，则打印消息并继续
                        print(f"文件或目录不存在: {file_path}")
                    except Exception as e:
                        # 打印其他类型的异常信息
                        print(f"删除 {file_path} 时发生错误: {e}")
        print("Cleaned directories. Sleeping for 1 minute.")
        # 等待一分钟
        time.sleep(60)

# 创建并启动清理线程
# clean_thread = threading.Thread(target=clean_directory)
# clean_thread.daemon = True  # 设置为守护线程
# clean_thread.start()

In [6]:
# 等待启动穿透
def requests_retry_session(retries=3, backoff_factor=0.3, status_forcelist=(500, 502, 504), session=None):
    session = session or requests.Session()
    retry = Retry(total=retries, backoff_factor=backoff_factor, status_forcelist=status_forcelist)
    adapter = HTTPAdapter(max_retries=retry)
    session.mount('http://', adapter)
    session.mount('https://', adapter)
    return session
def check_api1():
    while True:
        try:
            url = "http://127.0.0.1:7860/sdapi/v1/txt2img"
            response = requests.get(url, timeout=30)
            
            # 尝试解析返回的内容为 JSON
            try:
                response_json = response.json()
                # 检查返回的 JSON 是否为特定的错误信息
                if response_json.get("detail") in ("Method Not Allowed", "Not Found"):
                    print("SD已经启动")
                    break  # 接口正常，退出循环
                else:
                    print("SD未启动" )
            except json.JSONDecodeError:
                # 如果响应内容不是有效的 JSON，打印错误信息
                print("SD未启动2")
        
        except requests.exceptions.RequestException as e:
            # 如果请求出现异常（如网络问题），打印异常信息
            print("SD未启动3")
        
        # 无论是否发生异常，都等待一段时间后重试
        time.sleep(5)
    print('开始检测接口状态')
    while True:
        url = f"{sd_url}/sdapi/v1/txt2img"  # 修正URL
        try:
            response = requests_retry_session().get(url, timeout=30)
            response.raise_for_status()  # 将触发HTTPError，如果状态码不是200
            response_json = response.json()
            if "detail" in response_json and response_json["detail"] in ("Method Not Allowed", "Not Found"):
                print("接口正常")
            else:
                print("接口返回信息：", response_json)
        except requests.exceptions.HTTPError as e:
            print("接口正常2")
        except requests.exceptions.ConnectionError as e:
            print(f"接口异常1: {e}")
            if frp_status == 1:
                print("启动FRP")
                threading.Thread(target=Frpc, daemon=True).start()
            if nps_status == 1:
                print("启动NPS")
                threading.Thread(target=NPS, daemon=True).start()
            threading.Thread(target=run_script).start()
            #threading.Thread(target=run_commands).start()
            break
        except requests.exceptions.Timeout as e:
            print(f"接口异常2: {e}")
            if frp_status == 1:
                print("启动FRP")
                threading.Thread(target=Frpc, daemon=True).start()
            if nps_status == 1:
                print("启动NPS")
                threading.Thread(target=NPS, daemon=True).start()
            threading.Thread(target=run_script).start()
            #threading.Thread(target=run_commands).start()
            break
            
        except requests.exceptions.RequestException as e:
            print(f"接口异常3: {e}")
            if frp_status == 1:
                print("启动FRP")
                threading.Thread(target=Frpc, daemon=True).start()
            if nps_status == 1:
                print("启动NPS")
                threading.Thread(target=NPS, daemon=True).start()
            threading.Thread(target=run_script).start()
            #threading.Thread(target=run_commands).start()
            break
        time.sleep(5)
thread = threading.Thread(target=check_api1)
thread.daemon = True  # 非守护线程
thread.start()

SD未启动3
SD未启动3
SD未启动3
SD未启动3
SD未启动3
SD未启动3
SD未启动3
SD未启动3
SD未启动3
SD未启动3
SD未启动3
SD未启动3
SD未启动3
SD未启动3
SD未启动3
SD已经启动
开始检测接口状态
接口异常1: HTTPConnectionPool(host='119.8.118.149', port=8000): Max retries exceeded with url: /sdapi/v1/txt2img (Caused by ProtocolError('Connection aborted.', RemoteDisconnected('Remote end closed connection without response')))
启动NPS


In [7]:
# 创建一个HTML框用于显示输出
output_div = HTML("""
<div id='output' style='border: 1px solid black; padding: 10px; margin: 10px; height: 200px; overflow-y: auto;'>
</div>
""")
display(output_div)

# 定义JavaScript函数来更新输出
display(HTML("""
<script>
function updateOutput(content) {
    var output = document.getElementById('output');
    output.innerHTML += content + '<br>';
    output.scrollTop = output.scrollHeight;
}
</script>
"""))

def run_commands3(commands):
    for command in commands:
        try:
            # 显示当前执行的命令
            display(HTML(f"<script>updateOutput('执行命令: {command}')</script>"))
            
            # 执行命令
            process = subprocess.Popen(
                command,
                shell=True,
                stdout=subprocess.PIPE,
                stderr=subprocess.PIPE,
                text=True,
                bufsize=1,
                universal_newlines=True
            )
            
            # 实时读取并显示输出
            while True:
                output = process.stdout.readline().strip()
                if output == '' and process.poll() is not None:
                    break
                if output:
                    display(HTML(f"<script>updateOutput('{output}')</script>"))
            
            # 检查命令是否执行成功
            rc = process.poll()
            if rc != 0:
                display(HTML(f"<script>updateOutput('命令执行失败, 返回码: {rc}')</script>"))
        except Exception as e:
            display(HTML(f"<script>updateOutput('错误: {str(e)}')</script>"))


In [8]:
# 创建一个新的HTML框用于显示输出
new_output_div = HTML("""
<div id='new_output' style='border: 1px solid black; padding: 10px; margin: 10px; height: 200px; overflow-y: auto;'>
</div>
""")
display(new_output_div)

# 定义JavaScript函数来更新新的输出框
display(HTML("""
<script>
function updateNewOutput(content) {
    var output = document.getElementById('new_output');
    output.innerHTML += content + '<br>';
    output.scrollTop = output.scrollHeight;
}
</script>
"""))

def run_commands2(commands):
    for command in commands:
        try:
            # 显示当前执行的命令
            display(HTML(f"<script>updateNewOutput('执行命令: {command}')</script>"))
            
            # 执行命令
            process = subprocess.Popen(
                command,
                shell=True,
                stdout=subprocess.PIPE,
                stderr=subprocess.PIPE,
                text=True,
                bufsize=1,
                universal_newlines=True
            )
            
            # 实时读取并显示输出
            while True:
                output = process.stdout.readline().strip()
                if output == '' and process.poll() is not None:
                    break
                if output:
                    display(HTML(f"<script>updateNewOutput('{output}')</script>"))
            
            # 检查命令是否执行成功
            rc = process.poll()
            if rc != 0:
                display(HTML(f"<script>updateNewOutput('命令执行失败, 返回码: {rc}')</script>"))
        except Exception as e:
            display(HTML(f"<script>updateNewOutput('错误: {str(e)}')</script>"))


In [ ]:
def comfyui():
    run_commands3(['python /tmp/code/sd/ComfyUI/main.py'])
    #subprocess.run(["python", "/tmp/code/sd/ComfyUI/main.py"], check=True)
def server():
    !mr -r /tmp/code/main.py
    !wget -O /tmp/code/main.py 'https://hf-mirror.com/datasets/Qi28/SD_QZ/resolve/main/main.py'
    subprocess.run(["python", "/tmp/code/main.py"], check=True)
    #run_commands3(['python /tmp/code/main.py'])
threading.Thread(target=run_commands).start()
threading.Thread(target=server, daemon=True).start()
threading.Thread(target=comfyui, daemon=True).start()
!rm /tmp/code/sd/stable-diffusion-webui/config.json /tmp/code/*.log
!wget -O /tmp/code/sd/stable-diffusion-webui/config.json 'https://hf-mirror.com/datasets/Qilan28/hh_20240622/resolve/main/sd/config.json'
#--nowebui 
#run_commands2(['python /tmp/code/sd/stable-diffusion-webui/launch.py  --api --api-auth QiLan:1415361185 --no-hashing --enable-insecure-extension-access --no-gradio-queue --no-half-vae --port 7860 --xformers'])
!python /tmp/code/sd/stable-diffusion-webui/launch.py  --api --api-auth QiLan:1415361185 --no-hashing --enable-insecure-extension-access --no-gradio-queue --no-half-vae --port 7860 --xformers 

/usr/bin/sh: 1: mr: not found


--2024-11-22 02:55:47--  https://hf-mirror.com/datasets/Qilan28/hh_20240622/resolve/main/sd/config.json
Resolving hf-mirror.com (hf-mirror.com)... 160.16.199.204, 153.121.57.40, 133.242.169.68
Connecting to hf-mirror.com (hf-mirror.com)|160.16.199.204|:443... --2024-11-22 02:55:47--  https://hf-mirror.com/datasets/Qi28/SD_QZ/resolve/main/main.py
Resolving hf-mirror.com (hf-mirror.com)... 133.242.169.68, 153.121.57.40, 160.16.199.204
Connecting to hf-mirror.com (hf-mirror.com)|133.242.169.68|:443... Hit:1 https://mirrors.tuna.tsinghua.edu.cn/ubuntu jammy InRelease
connected.
Hit:3 https://mirrors.tuna.tsinghua.edu.cn/ubuntu jammy-updates InRelease
Hit:4 https://mirrors.tuna.tsinghua.edu.cn/ubuntu jammy-backports InRelease
connected.
HTTP request sent, awaiting response... HTTP request sent, awaiting response... Hit:2 https://developer.download.nvidia.cn/compute/cuda/repos/ubuntu2204/x86_64  InRelease
Get:5 http://security.ubuntu.com/ubuntu jammy-security InRelease [129 kB]


200 OK
Length: 16721 (16K) [text/plain]
Saving to: ‘/tmp/code/sd/stable-diffusion-webui/config.json’

/tmp/code/sd/stable 100%[===================>]  16.33K  --.-KB/s    in 0.05s   

2024-11-22 02:55:48 (307 KB/s) - ‘/tmp/code/sd/stable-diffusion-webui/config.json’ saved [16721/16721]

200 OK
Length: 6496 (6.3K) [text/plain]
Saving to: ‘/tmp/code/main.py’

/tmp/code/main.py   100%[===================>]   6.34K  --.-KB/s    in 0s      

2024-11-22 02:55:48 (94.1 MB/s) - ‘/tmp/code/main.py’ saved [6496/6496]

Hit:6 https://deb.nodesource.com/node_16.x nodistro InRelease
Python 3.10.12 (main, Jul 29 2024, 16:56:48) [GCC 11.4.0]
Version: v1.10.1
Commit hash: 82a973c04367123ae98bd9abdf80d9eda9b910e2


Cloning into '/tmp/code/sd/stable-diffusion-webui/extensions/stable-diffusion-webui-localization-zh_CN2.git'...


Fetched 129 kB in 2s (79.6 kB/s)
Reading package lists...
Building dependency tree...
Reading state information...
68 packages can be upgraded. Run 'apt list --upgradable' to see them.
Reading package lists...--------------远程执行---------------------
aria2c 已安装
--------------开始---------------------
已成功克隆仓库: stable-diffusion-webui-localization-zh_CN2.git
仓库 stable-diffusion-webui-images-browser 已存在, URL: https://github.com/AlUlkesh/stable-diffusion-webui-images-browser
仓库 AIGODLIKE-COMFYUI-TRANSLATION 已存在, URL: https://github.com/AIGODLIKE/AIGODLIKE-COMFYUI-TRANSLATION
仓库 comfyui-browser 已存在, URL: https://github.com/talesofai/comfyui-browser


...

 * Restarting OpenBSD Secure Shell server sshd
   ...done.


/usr/local/lib/python3.10/dist-packages/xformers/ops/fmha/flash.py:211: FutureWarning: `torch.library.impl_abstract` was renamed to `torch.library.register_fake`. Please use that instead; we will remove `torch.library.impl_abstract` in a future version of PyTorch.
  @torch.library.impl_abstract("xformers_flash::flash_fwd")
/usr/local/lib/python3.10/dist-packages/xformers/ops/fmha/flash.py:344: FutureWarning: `torch.library.impl_abstract` was renamed to `torch.library.register_fake`. Please use that instead; we will remove `torch.library.impl_abstract` in a future version of PyTorch.
  @torch.library.impl_abstract("xformers_flash::flash_bwd")
[-] ADetailer initialized. version: 24.11.1, num models: 10
找不到llama_cpp模块
sd-webui-prompt-all-in-one background API service started successfully.
Checkpoint 动漫-cetusMix_Whalefall2.safetensors not found; loading fallback 2.5D-CuriousMergeV5.safetensors
Loading weights [None] from /tmp/code/sd/stable-diffusion-webui/models/Stable-diffusion/2.5D-Curi

Latest version: v0.20.3
Loading VAE weights specified in settings: /tmp/code/sd/stable-diffusion-webui/models/VAE/ClearVAE.safetensors
Download completed. File saved to /tmp/code/nezha-agent.zip
Applying attention optimization: xformers... done.
Extraction completed.
Removed temporary zip file: /tmp/code/nezha-agent.zip


/tmp/code/sd/stable-diffusion-webui/modules/safe.py:156: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  return unsafe_torch_load(filename, *args, **kwargs)
Model loaded in 17

/tmp/code/sd/stable-diffusion-webui/modules/safe.py:156: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  return unsafe_torch_load(filename, *args, **kwargs)
100%|█████████████